# WBF $e^{+} e^{-} \to \nu \bar{\nu} h$

In [3]:
import random
import pandas as pd
import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import uproot3 as uproot

In [4]:
import xgboost as xgb
print(xgb.__version__)

1.2.0


In [5]:
signal = uproot.open("/media/dell/TishBackup2/higgs_lepton_colliders/cutflow_signunuh.root")['eventtree']
df_signal = signal.pandas.df(['vvh_*'])

In [6]:
background = uproot.open("/media/dell/TishBackup2/higgs_lepton_colliders/cutflow_bkgnunuh.root")['eventtree']
df_background = background.pandas.df(['vvh_*'])

In [7]:
df_signal=df_signal.assign(y=1)
df_background=df_background.assign(y=0)

In [8]:
df_list=[df_signal,df_background]
df=pd.concat(df_list)
df = df.reset_index()

In [9]:
dataset=df.values
X=dataset[:,0:7]#load only high level features
y=dataset[:,7]
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(X,y,test_size=0.20,random_state=45)

In [10]:
import xgboost as xgb
cls = xgb.XGBClassifier(base_score=0.5,
                       booster = 'gbtree',
                       colsample_bylevel=1,
                       colsample_bynode=1,
                       colsample_bytree=1,
                       gamma=0.0,
                       learning_rate = 0.1,
                       max_delta_step = 0,
                       max_depth = 4,
                       min_child_weight=50,
                       missing=None,
                       n_estimators=600,
                       n_jobs=-1,
                       n_thread=-1,
                       objective='binary:logistic',
                       random_state=0,
                       reg_alpha=0,
                       reg_lambda=1.2,
                       scale_pos_weight=1.0,
                       seed = None,
                       silent=None,
                       subsample=0.5,
                       verbosity=1)
#verbosity is showing more description

In [ ]:
cls.fit(X_train,y_train) #training
print('from train sample')
test_scores = cls.predict_proba(X_test)
train_scores = cls.predict_proba(X_train)

[19:43:57] WARNING: ../src/learner.cc:516: 
Parameters: { n_thread, scale_pos_weight } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.




In [ ]:
from sklearn.metrics import roc_curve,auc
fpr_tr,tpr_tr,thresholds_tr = roc_curve(y_train,train_scores[:,1],pos_label=None,sample_weight=None)
fpr_te,tpr_te,thresholds_te = roc_curve(y_test,test_scores[:,1],pos_label=None,sample_weight=None)

In [ ]:
train_auc = auc(fpr_tr,tpr_tr)
test_auc = auc(fpr_te,tpr_te)

In [ ]:
#ROC curve
fig,ax=plt.subplots(figsize=(5,5))
#ax.plot(tpr_tr,tpr_tr,lw=1,label='train(area-%0.3f)'%(train_auc))
ax.plot(tpr_tr,1-fpr_tr,lw=1,label='train(area-%0.3f)'%(train_auc))
ax.plot(tpr_te,1-fpr_te,lw=1,label='test(area-0.3%f)'%(test_auc))
ax.grid()
ax.legend(loc="lower weight")
ax.set_ylim([0.0,1.0])
ax.set_xlim([0.0,1.0])
ax.set_xlabel('signal efficiency')
ax.set_ylabel('background rejection')
fig.savefig("roc_xgb.png")